# Idea - (EN)

The idea is to be able to obtain a trained model using the family of T5 that allow us to parametrize the generation of texts.

Usually we will train using the text of poems, then we provide an starting text and obtain the generated one.

In this case we want to provide some parameters to control a the generation, if it is possible 😀

At the beginning the parameter can be the author, with the goal of generate text according to the style of the author.

Something like this:

```poema: estilo: <autor> && texto: <texto_inicial>```

If we manage to achieve this 🤞, then we can add more parameters like the sentiment that we want to obtain in the generated text, and some words that we want to include in the poem.

To be able to include more parameters we will need to add more information to the dataset like sentiment expressed and keywords.

# Idea - (ES)

La idea es poder obtener un modelo entrenado usando la familia T5 que nos permita parametrizar la generación de los textos.

Usualmente entrenamos usando los textos de los poemas, luego proveemos un texto inicial y de este el modelo obtenemos los textos generados.

En este caso vamos a proveer algunos parámetros para controlar la generación, si es posible 😀

Al inicio el parámetro puede ser el autor, con el objetivo de generar texto de acuerdo al estilo del autor.

Algo como esto:

```poema: estilo: <autor> && texto: <texto_inicial>```

Si logramos alcanzar esto 🤞, entonces podemos adicionar más parámetros como el sentimiento que queremos obtener en el texto generado, y algunas palabras que queremos que estén incluidas en el poema.

Para poder incluir más parámetros vamos a necesitar adicionar más información al dataset, sobre el sentimiento expresado y palabras claves.

# Install dependencies

In [19]:
!pip install -q transformers datasets sentencepiece

# Check GPU

In [20]:
!nvidia-smi 

Wed Mar 16 11:32:32 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.32.03    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla P100-PCIE...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   41C    P0    27W / 250W |      0MiB / 16280MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

## Free GPU

In case the GPU memory give you issues with memory space allocation, this cell can help you.

If repeteadly appears the problem, you will need to `Runtime > Restart runtime`. 
Try to lower the batch size in the TrainingArguments or activate the gradient_checkpointing to lower the required memory during training. 

The gradient_checkpointing will add more time to the computation. Some articles mention an overhead of 20%. 

In [21]:
import torch, gc
gc.collect()
torch.cuda.empty_cache()

# Parameters

In [22]:
#@title # Set global parameters

sel_model_name = 't5-small' #@param ['milyiyo/poem-gen-t5-small', 'flax-community/spanish-t5-small', "t5-small", "t5-base", "t5-larg", "t5-3b", "t5-11b"]
sel_num_train_epochs =  15 #@param {type:"number"}

# Download dataset

In [23]:
! wget --no-check-certificate 'https://docs.google.com/uc?export=download&id=1Rqfa-qC3Nm8oOMfnKjZYu6TF7iNg3Ju7' -O poems.csv

--2022-03-16 11:32:51--  https://docs.google.com/uc?export=download&id=1Rqfa-qC3Nm8oOMfnKjZYu6TF7iNg3Ju7
Resolving docs.google.com (docs.google.com)... 74.125.195.100, 74.125.195.138, 74.125.195.102, ...
Connecting to docs.google.com (docs.google.com)|74.125.195.100|:443... connected.
HTTP request sent, awaiting response... 303 See Other
Location: https://doc-0s-4s-docs.googleusercontent.com/docs/securesc/ha0ro937gcuc7l7deffksulhg5h7mbp1/jagb31d4n9oluej1342h2s3s8dc9f81d/1647430350000/13706297538515163693/*/1Rqfa-qC3Nm8oOMfnKjZYu6TF7iNg3Ju7?e=download [following]
--2022-03-16 11:32:53--  https://doc-0s-4s-docs.googleusercontent.com/docs/securesc/ha0ro937gcuc7l7deffksulhg5h7mbp1/jagb31d4n9oluej1342h2s3s8dc9f81d/1647430350000/13706297538515163693/*/1Rqfa-qC3Nm8oOMfnKjZYu6TF7iNg3Ju7?e=download
Resolving doc-0s-4s-docs.googleusercontent.com (doc-0s-4s-docs.googleusercontent.com)... 74.125.195.132, 2607:f8b0:400e:c09::84
Connecting to doc-0s-4s-docs.googleusercontent.com (doc-0s-4s-docs.goog

# Import dependencies

In [24]:
import pandas as pd
import os
import torch
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM, Seq2SeqTrainingArguments, DataCollatorForSeq2Seq, Seq2SeqTrainer
from datasets import load_dataset, Dataset, DatasetDict
import time
import math
from pprint import pprint
import warnings
warnings.filterwarnings('ignore')

# Prepare dataset

In [25]:
dataset = load_dataset('csv', data_files='poems.csv')
dataset

Using custom data configuration default-b2da644438462884


Extracting data files:   0%|          | 0/1 [00:00<?, ?it/s]

Dataset csv downloaded and prepared to /root/.cache/huggingface/datasets/csv/default-b2da644438462884/0.0.0/433e0ccc46f9880962cc2b12065189766fbb2bee57a221866138fb9203c83519. Subsequent calls will reuse this data.


  0%|          | 0/1 [00:00<?, ?it/s]

DatasetDict({
    train: Dataset({
        features: ['author', 'content', 'title'],
        num_rows: 5133
    })
})

## Generate a new dataset 

In [26]:
res_dict = {
    'paragraph': [],
    'author': [],
    'generated': []
}

for train_row in dataset['train']:
  author = train_row['author']
  content = train_row['content']
  if content is None:
    continue
  content = content.replace('\n\n', '<SPLIT>')
  content = content.replace('\n', '<SPLIT>')
  paragraphs = content.split('<SPLIT>')
  res = []

  for i in range(0, len(paragraphs)-1, 2):
    res.append(paragraphs[i] + ' ' + paragraphs[i+1])
    i+=1

  paragraphs = res

  for i in range(len(paragraphs)-1):
    res_dict['paragraph'] += [paragraphs[i]]
    res_dict['author'] += [author]
    res_dict['generated'] += [paragraphs[i+1]]

In [27]:
new_ds = Dataset.from_dict(res_dict)
new_ds

Dataset({
    features: ['paragraph', 'author', 'generated'],
    num_rows: 70386
})

In [28]:
new_ds[1]

{'author': 'Leopoldo Lugones',
 'generated': 'Devana un ovillo de de bruma. El telar de la luna tiende en plata su urdimbre;',
 'paragraph': 'Que con lánguidas brisas el cielo sahúma, El ciprés, como un huso,'}

## Load model and tokenizer

In [29]:
tokenizer = AutoTokenizer.from_pretrained(sel_model_name)
model = AutoModelForSeq2SeqLM.from_pretrained(sel_model_name)

## Tokenize dataset

In [30]:
def prepare_input_text_v2(example):
  author = example['author']
  text = example['paragraph']
  template = f"""poema: estilo: {author} && texto: {text}"""
  example['input'] = template
  return example

dataset_pre = new_ds.map(prepare_input_text_v2)
dataset_pre

  0%|          | 0/70386 [00:00<?, ?ex/s]

Dataset({
    features: ['paragraph', 'author', 'generated', 'input'],
    num_rows: 70386
})

In [31]:
dataset_pre[1]

{'author': 'Leopoldo Lugones',
 'generated': 'Devana un ovillo de de bruma. El telar de la luna tiende en plata su urdimbre;',
 'input': 'poema: estilo: Leopoldo Lugones && texto: Que con lánguidas brisas el cielo sahúma, El ciprés, como un huso,',
 'paragraph': 'Que con lánguidas brisas el cielo sahúma, El ciprés, como un huso,'}

In [32]:
def preprocess_function(ex):
  inputs = ex["input"]
  targets = ex["generated"]
  model_inputs = tokenizer(inputs, truncation=True)

  # Set up the tokenizer for targets
  with tokenizer.as_target_tokenizer():
      labels = tokenizer(targets, truncation=True)

  model_inputs["labels"] = labels["input_ids"]
  return model_inputs

In [33]:
dataset_inputs_labels_v2 = dataset_pre.map(preprocess_function, remove_columns=dataset_pre.column_names )
dataset_inputs_labels_v2

  0%|          | 0/70386 [00:00<?, ?ex/s]

Dataset({
    features: ['input_ids', 'attention_mask', 'labels'],
    num_rows: 70386
})

In [34]:
test_count = int(70386 * .1)
dict_test = dataset_inputs_labels_v2[:test_count]
dict_train = dataset_inputs_labels_v2[test_count:]

ds_test = Dataset.from_dict(dict_test)
ds_train = Dataset.from_dict(dict_train)

# Training arguments

In [36]:
if sel_model_name.startswith('milyiyo'):
  output_dir = sel_model_name.split('/')[1]
else:
  output_dir = 'poem-gen-'+sel_model_name.split('/')[0]+"_v1"

[output_dir, sel_model_name]

['poem-gen-t5-small_v1', 't5-small']

In [37]:
training_args = Seq2SeqTrainingArguments(
    output_dir=output_dir,
    learning_rate=5e-5,
    per_device_train_batch_size=4,
    per_device_eval_batch_size=4,
    num_train_epochs=sel_num_train_epochs,
    weight_decay=.0, #0.0,
    save_total_limit = 5,
    save_steps=5000,
    save_strategy = 'steps',
    eval_steps=5000, # new
    evaluation_strategy ='steps',
    predict_with_generate=True,
    logging_steps = 1000,
    push_to_hub = True,
    # gradient_checkpointing=True # In case the model does not fit in the GPU's memory
)

# Connect to HuggingFace

In [38]:
!huggingface-cli login


        _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
        _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
        _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
        _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
        _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|

        To login, `huggingface_hub` now requires a token generated from https://huggingface.co/settings/token.
        (Deprecated, will be removed in v0.3.0) To login with username and password instead, interrupt with Ctrl+C.
        
Token: 
Login successful
Your token has been saved to /root/.huggingface/token
Authenticated through git-credential store but this isn't the helper defined on your machine

In [39]:
!git config --global credential.helper store

In [40]:
!apt-get install git-lfs
!git lfs install

Reading package lists... Done
Building dependency tree       
Reading state information... Done
The following NEW packages will be installed:
  git-lfs
0 upgraded, 1 newly installed, 0 to remove and 39 not upgraded.
Need to get 2,129 kB of archives.
After this operation, 7,662 kB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu bionic/universe amd64 git-lfs amd64 2.3.4-1 [2,129 kB]
Fetched 2,129 kB in 1s (1,630 kB/s)
Selecting previously unselected package git-lfs.
(Reading database ... 155335 files and directories currently installed.)
Preparing to unpack .../git-lfs_2.3.4-1_amd64.deb ...
Unpacking git-lfs (2.3.4-1) ...
Setting up git-lfs (2.3.4-1) ...
Processing triggers for man-db (2.8.3-2ubuntu0.1) ...
Error: Failed to call git rev-parse --git-dir --show-toplevel: "fatal: not a git repository (or any of the parent directories): .git\n"
Git LFS initialized.


# Trainer

In [41]:
data_collator = DataCollatorForSeq2Seq(tokenizer, model)

trainer = Seq2SeqTrainer(
    model,
    args=training_args,
    train_dataset= ds_train,
    eval_dataset= ds_test,
    data_collator=data_collator,
    tokenizer=tokenizer,
)

Cloning https://huggingface.co/DrishtiSharma/poem-gen-t5-small_v1 into local empty directory.


## Check perplexity

In [42]:
eval_results = trainer.evaluate()
print(f"Perplexity: {math.exp(eval_results['eval_loss']):.2f}")

***** Running Evaluation *****
  Num examples = 7038
  Batch size = 4


Perplexity: 60.06


# Train the model

In [43]:
trainer.train(resume_from_checkpoint=False)

***** Running training *****
  Num examples = 63348
  Num Epochs = 15
  Instantaneous batch size per device = 4
  Total train batch size (w. parallel, distributed & accumulation) = 4
  Gradient Accumulation steps = 1
  Total optimization steps = 237555


***** Running Evaluation *****
  Num examples = 7038
  Batch size = 4


Saving model checkpoint to poem-gen-t5-small_v1/checkpoint-5000
Configuration saved in poem-gen-t5-small_v1/checkpoint-5000/config.json
Model weights saved in poem-gen-t5-small_v1/checkpoint-5000/pytorch_model.bin
tokenizer config file saved in poem-gen-t5-small_v1/checkpoint-5000/tokenizer_config.json
Special tokens file saved in poem-gen-t5-small_v1/checkpoint-5000/special_tokens_map.json
Copy vocab file to poem-gen-t5-small_v1/checkpoint-5000/spiece.model
tokenizer config file saved in poem-gen-t5-small_v1/tokenizer_config.json
Special tokens file saved in poem-gen-t5-small_v1/special_tokens_map.json
Copy vocab file to poem-gen-t5-small_v1/spiece.model
***** Running Evaluation *****
  Num examples = 7038
  Batch size = 4
Saving model checkpoint to poem-gen-t5-small_v1/checkpoint-10000
Configuration saved in poem-gen-t5-small_v1/checkpoint-10000/config.json
Model weights saved in poem-gen-t5-small_v1/checkpoint-10000/pytorch_model.bin
tokenizer config file saved in poem-gen-t5-small_

TrainOutput(global_step=237555, training_loss=2.936270662464186, metrics={'train_runtime': 19337.8395, 'train_samples_per_second': 49.138, 'train_steps_per_second': 12.284, 'total_flos': 1.5501099375919104e+16, 'train_loss': 2.936270662464186, 'epoch': 15.0})

## Check perplexity

In [44]:
eval_results = trainer.evaluate()
print(f"Perplexity: {math.exp(eval_results['eval_loss']):.2f}")

***** Running Evaluation *****
  Num examples = 7038
  Batch size = 4


Perplexity: 15.32


## Push to Hub

In [45]:
trainer.push_to_hub()

Saving model checkpoint to poem-gen-t5-small_v1
Configuration saved in poem-gen-t5-small_v1/config.json
Model weights saved in poem-gen-t5-small_v1/pytorch_model.bin
tokenizer config file saved in poem-gen-t5-small_v1/tokenizer_config.json
Special tokens file saved in poem-gen-t5-small_v1/special_tokens_map.json
Copy vocab file to poem-gen-t5-small_v1/spiece.model
Several commits (2) will be pushed upstream.
The progress bars may be unreliable.


Upload file pytorch_model.bin:   0%|          | 3.34k/231M [00:00<?, ?B/s]

Upload file runs/Mar16_11-37-02_afdd3546723d/events.out.tfevents.1647450084.afdd3546723d.84.2: 100%|##########…

Upload file runs/Mar16_11-37-02_afdd3546723d/events.out.tfevents.1647430712.afdd3546723d.84.0:   6%|6         …

remote: tput: No value for $TERM and no -T specified        
remote: tput: No value for $TERM and no -T specified
remote: tput: No value for $TERM and no -T specified        
remote: tput: No value for $TERM and no -T specified        
To https://huggingface.co/DrishtiSharma/poem-gen-t5-small_v1
   d2b277b..42c41b3  main -> main

Dropping the following result as it does not have all the necessary fields:
{'task': {'name': 'Sequence-to-sequence Language Modeling', 'type': 'text2text-generation'}}
remote: tput: No value for $TERM and no -T specified        
remote: tput: No value for $TERM and no -T specified        
remote: tput: No value for $TERM and no -T specified        
remote: tput: No value for $TERM and no -T specified        
To https://huggingface.co/DrishtiSharma/poem-gen-t5-small_v1
   42c41b3..5d6100f  main -> main



'https://huggingface.co/DrishtiSharma/poem-gen-t5-small_v1/commit/42c41b39d13cd739a75fa71aad67ff1a56d601ba'

# Test the model

In [46]:
# model_trained = AutoModelForSeq2SeqLM.from_pretrained('poem-gen-'+sel_model_name.split('/')[0])
model_trained = AutoModelForSeq2SeqLM.from_pretrained('DrishtiSharma/'+output_dir)

https://huggingface.co/DrishtiSharma/poem-gen-t5-small_v1/resolve/main/config.json not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmpumxug7t6


Downloading:   0%|          | 0.00/1.35k [00:00<?, ?B/s]

storing https://huggingface.co/DrishtiSharma/poem-gen-t5-small_v1/resolve/main/config.json in cache at /root/.cache/huggingface/transformers/5a92d92cc6b0f0d6d9f6a0bf0aac25eb9d9c3077436330dcb1cdcbf26543f823.d1b447d2d77f64965845e2315488ade5473578846e926f3195a1a9e440231045
creating metadata file for /root/.cache/huggingface/transformers/5a92d92cc6b0f0d6d9f6a0bf0aac25eb9d9c3077436330dcb1cdcbf26543f823.d1b447d2d77f64965845e2315488ade5473578846e926f3195a1a9e440231045
loading configuration file https://huggingface.co/DrishtiSharma/poem-gen-t5-small_v1/resolve/main/config.json from cache at /root/.cache/huggingface/transformers/5a92d92cc6b0f0d6d9f6a0bf0aac25eb9d9c3077436330dcb1cdcbf26543f823.d1b447d2d77f64965845e2315488ade5473578846e926f3195a1a9e440231045
Model config T5Config {
  "_name_or_path": "DrishtiSharma/poem-gen-t5-small_v1",
  "architectures": [
    "T5ForConditionalGeneration"
  ],
  "d_ff": 2048,
  "d_kv": 64,
  "d_model": 512,
  "decoder_start_token_id": 0,
  "dropout_rate": 0.1,


Downloading:   0%|          | 0.00/231M [00:00<?, ?B/s]

storing https://huggingface.co/DrishtiSharma/poem-gen-t5-small_v1/resolve/main/pytorch_model.bin in cache at /root/.cache/huggingface/transformers/8675216690d506b55b323d7ef2499a4e45494e1a2cc43f4eee0d6e84d56baed1.f127ffe6e291b37e7ec8c1c53d89a62cc87a258975081b9c60eddde04d4a402d
creating metadata file for /root/.cache/huggingface/transformers/8675216690d506b55b323d7ef2499a4e45494e1a2cc43f4eee0d6e84d56baed1.f127ffe6e291b37e7ec8c1c53d89a62cc87a258975081b9c60eddde04d4a402d
loading weights file https://huggingface.co/DrishtiSharma/poem-gen-t5-small_v1/resolve/main/pytorch_model.bin from cache at /root/.cache/huggingface/transformers/8675216690d506b55b323d7ef2499a4e45494e1a2cc43f4eee0d6e84d56baed1.f127ffe6e291b37e7ec8c1c53d89a62cc87a258975081b9c60eddde04d4a402d
All model checkpoint weights were used when initializing T5ForConditionalGeneration.

All the weights of T5ForConditionalGeneration were initialized from the model checkpoint at DrishtiSharma/poem-gen-t5-small_v1.
If your task is simila

In [51]:
authors = ['leopoldo lugones', 'juan ramón jiménez']
start_texts = [
               'que con lánguidas brisas el cielo sahúma, el ciprés, como un huso, ',
               'todos fueron al parque a verla pasar, todos estaban esperando esa hora '  
]
start_text = start_texts[1]
author = authors[1]
input_text = f"""poema: estilo: {author} && texto: {start_text}</s>"""

inputs = tokenizer(input_text, return_tensors="pt")

In [52]:
model_outputs = model_trained.generate(inputs["input_ids"], max_length=100, num_beams=4, early_stopping=True,
                          repetition_penalty=20.0, num_return_sequences=2)
for output in model_outputs:
  print(tokenizer.decode(output, skip_special_tokens=True))

y todos estaban despertando. Todos fueron al parque,
y todos estaban despertar. Todos fueron al parque


In [53]:
def make_poem_v1(author, text, num_lines=5, avoid_repeated_outputs=True, repetition_penalty=10.0, num_beams=4):
  input_text = f"""poema: estilo: {author} && texto: {text} """
  inputs = tokenizer(input_text, return_tensors="pt")
  print(text)

  prev_output = ''
  for i in range(num_lines):
    outputs = model_trained.generate(inputs["input_ids"], 
                                     max_length=100, 
                                     num_beams=num_beams, 
                                     early_stopping=False,
                                     do_sample=True,
                                     temperature=.7,
                                     repetition_penalty=repetition_penalty, 
                                     num_return_sequences=num_beams)
    detok_outputs = [tokenizer.decode(x, skip_special_tokens=True) for x in outputs]
    pre_output = detok_outputs[0]
    
    if avoid_repeated_outputs:
      # Choose an output different from the previous one
      for item in detok_outputs:
        # print('    ' + item)
        if item == prev_output:
          continue
        pre_output = item

    pre_output = pre_output.replace('.', ' ')
    print(pre_output)
    new_input = f"""poema: estilo: {author} && texto: {pre_output}"""
    inputs = tokenizer(new_input, return_tensors="pt")
    prev_output = pre_output

In [54]:
make_poem_v1(author='leopoldo lugones',
             text='la luz se prendió cuando la tarde cayó, la luna asomó su rostro y una estrella le sonrió',
             num_lines=5,
             avoid_repeated_outputs=True,
             repetition_penalty=20.0, 
             num_beams=4)

la luz se prendió cuando la tarde cayó, la luna asomó su rostro y una estrella le sonrió
y una sombra le dijo: «Quién me quedó!»  Aqu se detiene
aqu se detiene  No me quedó,
ni me quedó  No,
ni me quedó No,
ni me quedó No, no puede
